# 1. Load data and libraries

In [35]:
import pandas as pd
from tabulate import tabulate
import pandas as pd
import matplotlib.pyplot as plt
import plotly.express as px
import seaborn as sns
from matplotlib.ticker import FuncFormatter
from matplotlib.ticker import StrMethodFormatter

In [36]:
def print_df(df, len = 5):
    print(tabulate(df.head(len),headers=df.columns, tablefmt='pswl'))

def convert_date_denomination(df, date_column = 'Date of Purchase', denomination_column = 'Denomination'):
    df[date_column] = pd.to_datetime(df[date_column], format='%d/%b/%Y')
    df[denomination_column] = df[denomination_column].str.replace(',', '').astype(int)
    return df


## 1.1 Company data

In [37]:
df_company = pd.read_csv("purchaser_bonds1.csv")
df_company = df_company.rename(columns={"Denomination": "CompanyDenomination"})
print_df(df_company)
print("Shape of company dataframe", df_company.shape)

    Date of Purchase    Purchaser Name       CompanyDenomination
--  ------------------  -------------------  ---------------------
 0  12/Apr/2019         A B C INDIA LIMITED  1,00,000
 1  12/Apr/2019         A B C INDIA LIMITED  1,00,000
 2  12/Apr/2019         A B C INDIA LIMITED  10,00,000
 3  12/Apr/2019         A B C INDIA LIMITED  10,00,000
 4  12/Apr/2019         A B C INDIA LIMITED  1,00,000
Shape of company dataframe (16609, 3)


In [38]:
df_company = convert_date_denomination(df_company, "Date of Purchase", "CompanyDenomination")
df_company.dtypes


Date of Purchase       datetime64[ns]
Purchaser Name                 object
CompanyDenomination             int64
dtype: object

## 1.2 Party data

In [39]:
df_party = pd.read_csv("tabula-e-bonds2.csv")
df_party = df_party.rename(columns={"Date of\rEncashment": "Date of Encashment", "Denomination": "PartyDenomination"})
print_df(df_party)
print("Shape of party dataframe",df_party.shape)

FileNotFoundError: [Errno 2] No such file or directory: 'tabula-e-bonds2.csv'

In [ ]:
df_party = convert_date_denomination(df_party, "Date of Encashment", "PartyDenomination")
df_party.dtypes

Date of Encashment             datetime64[ns]
Name of the Political Party            object
PartyDenomination                       int64
dtype: object

## 1.3 Merging the data from both dataframes

In [ ]:
concatenated_df = pd.concat([df_party, df_company], ignore_index=True)
concatenated_df = concatenated_df.sort_values(by="Date of Encashment")
print_df(concatenated_df)

     Date of Encashment    Name of the Political Party                 PartyDenomination  Date of Purchase      Purchaser Name    CompanyDenomination
---  --------------------  ----------------------------------------  -------------------  ------------------  ----------------  ---------------------
  0  2019-04-12 00:00:00   ALL INDIA ANNA DRAVIDA MUNNETRA KAZHAGAM                1e+06  NaT                              nan                    nan
347  2019-04-12 00:00:00   BHARTIYA JANTA PARTY                                    1e+06  NaT                              nan                    nan
346  2019-04-12 00:00:00   BHARTIYA JANTA PARTY                                    1e+06  NaT                              nan                    nan
345  2019-04-12 00:00:00   BHARTIYA JANTA PARTY                                    1e+07  NaT                              nan                    nan
344  2019-04-12 00:00:00   BHARTIYA JANTA PARTY                                    1e+07  NaT       

# 2. EDA - Company
We will perform EDA analysis on the company data. We will create new dataframes for ease of interaction and plotting.

## 2.1 Company data exploration

In [ ]:
print(df_company.nunique())
print("================================", end = "\n")

print("Unique values of denominations:")
print(df_company['CompanyDenomination'].value_counts())
print("================================", end = "\n")

df_company.info()

Date of Purchase        139
Purchaser Name         1223
CompanyDenomination       5
dtype: int64
Unique values of denominations:
10000000    10438
1000000      4151
100000       1714
10000         180
1000          126
Name: CompanyDenomination, dtype: int64
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 16609 entries, 0 to 16608
Data columns (total 3 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   Date of Purchase     16609 non-null  datetime64[ns]
 1   Purchaser Name       16609 non-null  object        
 2   CompanyDenomination  16609 non-null  int64         
dtypes: datetime64[ns](1), int64(1), object(1)
memory usage: 389.4+ KB


In [ ]:
# create a new DataFrame with Purchaser Name and CombinedDenomination
df_combinedDenomination = df_company.groupby('Purchaser Name')['CompanyDenomination'].sum().reset_index()
df_combinedDenomination.columns = ['Purchaser Name', 'CombinedDenomination']

print("New DataFrame with Purchaser Name and CombinedDenomination:")
print_df(df_combinedDenomination)
print()

# group transactions by Purchaser Name and Date and sum up CompanyDenomination
df_company['Date of Purchase'] = pd.to_datetime(df_company['Date of Purchase']).dt.date  # Convert to date only
df_daywiseTransactions = df_company.groupby(['Purchaser Name', 'Date of Purchase'])['CompanyDenomination'].agg(['sum', 'count']).reset_index()
df_daywiseTransactions.columns = ['Purchaser Name', 'Date of Purchase', 'TotalDenomination', 'TotalTransactions']
# adding year and quarter columns
df_daywiseTransactions['Year'] = pd.to_datetime(df_daywiseTransactions['Date of Purchase']).dt.year
df_daywiseTransactions['Quarter'] = pd.to_datetime(df_daywiseTransactions['Date of Purchase']).dt.quarter

print("New DataFrame grouped by Purchaser Name and Date with total denomination and total transactions:")
print_df(df_daywiseTransactions)


New DataFrame with Purchaser Name and CombinedDenomination:
    Purchaser Name                        CombinedDenomination
--  ----------------------------------  ----------------------
 0  14 REELS PLUS LLP                                 10000000
 1  A B C INDIA LIMITED                                4000000
 2  AAKANKSHA BAHETY                                   1000000
 3  AALAYA CONSTRUCTIONS                              10000000
 4  AARISH SOLAR POWER PRIVATE LIMITED                20000000

New DataFrame grouped by Purchaser Name and Date with total denomination and total transactions:
    Purchaser Name                      Date of Purchase      TotalDenomination    TotalTransactions    Year    Quarter
--  ----------------------------------  ------------------  -------------------  -------------------  ------  ---------
 0  14 REELS PLUS LLP                   2022-04-08                     10000000                    1    2022          2
 1  A B C INDIA LIMITED                 2

Functions needed for plotting data throughout the notebook for Company Data

In [ ]:
# Function to plot quarterly data
def plot_quarterly_data_company(df, year):
    df_year = df[df['Year'] == year].copy()
    df_year['purchase_count'] = 1

    df_quarterly = df_year.groupby(['Quarter', 'Purchaser Name']).agg({
        'TotalDenomination': 'sum',
        'TotalTransactions': 'sum',
        'purchase_count': 'sum'
    }).reset_index()

    df_quarterly = df_quarterly.rename(columns={
        'TotalDenomination': 'quarterly_transaction_value',
        'TotalTransactions': 'quarterly_purchase_count'
    })

    sorted_purchasers = df_quarterly.groupby('Purchaser Name')['quarterly_transaction_value'].sum().sort_values(ascending=False).index

    fig1 = px.bar(df_quarterly, x='Quarter', y='quarterly_transaction_value', color='Purchaser Name',
                  title=f'Quarterly Transaction Value by Purchaser Name - {year}',
                  labels={'Quarter': 'Quarter', 'quarterly_transaction_value': 'Transaction Value',
                          'Purchaser Name': 'Purchaser Name'},
                  category_orders={'Purchaser Name': sorted_purchasers})
    fig1.show()

    fig2 = px.bar(df_quarterly, x='Quarter', y='quarterly_purchase_count', color='Purchaser Name',
                  title=f'Quarterly Purchase Count by Purchaser Name - {year}',
                  labels={'Quarter': 'Quarter', 'quarterly_purchase_count': 'Purchase Count',
                          'Purchaser Name': 'Purchaser Name'},
                  category_orders={'Purchaser Name': sorted_purchasers})
    fig2.show()
def plot_yearly_data_company(df, year, data_column, title_prefix):
    df_year = df[df['Year'] == year].copy()
    sorted_purchasers = df_year.groupby('Purchaser Name')[data_column].sum().sort_values(ascending=False).index
    fig = px.bar(df_year, x='Date of Purchase', y=data_column, color='Purchaser Name',
                 title=f'{title_prefix} - {year}',
                 labels={'Date of Purchase': 'Date', data_column: title_prefix,
                         'Purchaser Name': 'Purchaser Name'},
                 category_orders={'Purchaser Name': sorted_purchasers})
    fig.update_layout(height=800, width=1000)
    fig.update_xaxes(type='category')
    fig.show()

def plot_yearly_data_combined_company(df_daywiseTransactions):
    unique_years = sorted(df_daywiseTransactions['Year'].unique())
    for year in unique_years:
        plot_yearly_data_company(df_daywiseTransactions, year, 'TotalDenomination', 'Yearly Transaction Value by Purchaser Name')
        plot_yearly_data_company(df_daywiseTransactions, year, 'TotalTransactions', 'Yearly Purchase Count by Purchaser Name')
        print("============================================================ End of Year ", year, "============================================================")


def create_cumulative_purchase_treemap_company(df_combinedDenomination, df_daywiseTransactions):
    # top 30 purchasers based on maximum purchase count
    top_purchasers = df_daywiseTransactions.groupby('Purchaser Name')['TotalTransactions'].max().nlargest(30).index
    df_top30 = df_daywiseTransactions[df_daywiseTransactions['Purchaser Name'].isin(top_purchasers)]

    # Merging df_top30 with df_combinedDenomination to include CombinedDenomination
    df_merged = pd.merge(df_top30, df_combinedDenomination, on='Purchaser Name', how='left')

    fig = px.treemap(df_merged, path=['Purchaser Name', 'Date of Purchase'], values='TotalDenomination', color='TotalDenomination',
                     title='Total Transaction Value Over Time for Top 30 Companies',
                     labels={'TotalDenomination': 'Total Transaction Value', 'TotalTransactions': 'Cumulative Purchase Count'},
                     hover_data={'TotalDenomination': True, 'TotalTransactions': True},
                     width=1000, height=1000)
    return fig


## 2.2 Company Data Visualization 

### Plot 2.2.a: Quarterly Transaction Value and Quarterly Transaction Frequency by the companies

In [ ]:

# unique years from df_daywiseTransactions and iterate over each year and plot quarterly data
unique_years = sorted(df_daywiseTransactions['Year'].unique())
for year in unique_years:
    plot_quarterly_data_company(df_daywiseTransactions, year)

### Plot2.2.b: Yearly Transaction Value and Yearly Transaction Frequency by the companies

In [ ]:
plot_yearly_data_combined_company(df_daywiseTransactions)

============================================================ End of Year  2019 ============================================================


============================================================ End of Year  2020 ============================================================


============================================================ End of Year  2021 ============================================================


============================================================ End of Year  2022 ============================================================


============================================================ End of Year  2023 ============================================================


============================================================ End of Year  2024 ============================================================


### Plot 2.2.c: Total Transaction Value Over Time for Top 30 Companies

In [ ]:
fig = create_cumulative_purchase_treemap_company(df_combinedDenomination, df_daywiseTransactions)
fig.show()


# 3. EDA - Political Party

## 3.1 Party data exploration

In [ ]:
print_df(df_party)

    Date of Encashment    Name of the Political Party                 PartyDenomination
--  --------------------  ----------------------------------------  -------------------
 0  2019-04-12 00:00:00   ALL INDIA ANNA DRAVIDA MUNNETRA KAZHAGAM              1000000
 1  2019-04-12 00:00:00   ALL INDIA ANNA DRAVIDA MUNNETRA KAZHAGAM              1000000
 2  2019-04-12 00:00:00   ALL INDIA ANNA DRAVIDA MUNNETRA KAZHAGAM             10000000
 3  2019-04-12 00:00:00   ALL INDIA ANNA DRAVIDA MUNNETRA KAZHAGAM              1000000
 4  2019-04-12 00:00:00   ALL INDIA ANNA DRAVIDA MUNNETRA KAZHAGAM              1000000


In [ ]:
print(df_party.nunique())

print("================================", end = "\n")
print("Unique values of denominations:")
print(df_party['PartyDenomination'].value_counts())

print("================================", end = "\n")
df_party.info()

Date of Encashment             230
Name of the Political Party     27
PartyDenomination                5
dtype: int64
Unique values of denominations:
10000000    11956
1000000      5257
100000       2467
10000         215
1000          100
Name: PartyDenomination, dtype: int64
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19995 entries, 0 to 19994
Data columns (total 3 columns):
 #   Column                       Non-Null Count  Dtype         
---  ------                       --------------  -----         
 0   Date of Encashment           19995 non-null  datetime64[ns]
 1   Name of the Political Party  19995 non-null  object        
 2   PartyDenomination            19995 non-null  int64         
dtypes: datetime64[ns](1), int64(1), object(1)
memory usage: 468.8+ KB


In [ ]:
# A new DataFrame with Name of the Political Party and CombinedDenomination
df_combinedDenomination_party = df_party.groupby('Name of the Political Party')['PartyDenomination'].sum().reset_index()
df_combinedDenomination_party.columns = ['Name of the Political Party', 'CombinedDenomination']

print("New DataFrame with Name of the Political Party and CombinedDenomination:")
print_df(df_combinedDenomination_party)
print()

#group transactions by Name of the Political Party and Date and sum up PartyDenomination
df_daywiseTransactions_party = df_party.groupby(['Name of the Political Party', 'Date of Encashment'])['PartyDenomination'].agg(['sum', 'count']).reset_index()
df_daywiseTransactions_party.columns = ['Name of the Political Party', 'Date of Encashment', 'TotalDenomination', 'TotalTransactions']
#adding year and quarter columns
df_daywiseTransactions_party['Year'] = pd.to_datetime(df_daywiseTransactions_party['Date of Encashment']).dt.year
df_daywiseTransactions_party['Quarter'] = pd.to_datetime(df_daywiseTransactions_party['Date of Encashment']).dt.quarter

print("new DataFrame grouped by Name of the Political Party and Date with total denomination and total transactions:")
print_df(df_daywiseTransactions_party)


New DataFrame with Name of the Political Party and CombinedDenomination:
    Name of the Political Party                 CombinedDenomination
--  ----------------------------------------  ----------------------
 0  AAM AADMI PARTY                                        653300000
 1  ADYAKSHA SAMAJVADI PARTY                               140500000
 2  ALL INDIA ANNA DRAVIDA MUNNETRA KAZHAGAM                60500000
 3  ALL INDIA TRINAMOOL CONGRESS                         15754813000
 4  BHARAT RASHTRA SAMITHI                               11930398000

new DataFrame grouped by Name of the Political Party and Date with total denomination and total transactions:
    Name of the Political Party    Date of Encashment      TotalDenomination    TotalTransactions    Year    Quarter
--  -----------------------------  --------------------  -------------------  -------------------  ------  ---------
 0  AAM AADMI PARTY                2019-04-18 00:00:00               2000000                    2  

Functions needed for plotting data throughout the notebook for Political Party Data

In [ ]:
# Function to plot quarterly data
def plot_quarterly_data(df, year):
    df_year = df[df['Year'] == year].copy()
    df_year['purchase_count'] = 1

    df_quarterly = df_year.groupby(['Quarter', 'Name of the Political Party']).agg({
        'TotalDenomination': 'sum',
        'TotalTransactions': 'sum',
        'purchase_count': 'sum'
    }).reset_index()

    df_quarterly = df_quarterly.rename(columns={
        'TotalDenomination': 'quarterly_transaction_value',
        'TotalTransactions': 'quarterly_purchase_count'
    })

    sorted_purchasers = df_quarterly.groupby('Name of the Political Party')['quarterly_transaction_value'].sum().sort_values(ascending=False).index

    fig1 = px.bar(df_quarterly, x='Quarter', y='quarterly_transaction_value', color='Name of the Political Party',
                  title=f'Quarterly Transaction Value by Name of the Political Party - {year}',
                  labels={'Quarter': 'Quarter', 'quarterly_transaction_value': 'Transaction Value',
                          'Name of the Political Party': 'Name of the Political Party'},
                  category_orders={'Name of the Political Party': sorted_purchasers})
    fig1.show()

    fig2 = px.bar(df_quarterly, x='Quarter', y='quarterly_purchase_count', color='Name of the Political Party',
                  title=f'Quarterly Purchase Count by Name of the Political Party - {year}',
                  labels={'Quarter': 'Quarter', 'quarterly_purchase_count': 'Purchase Count',
                          'Name of the Political Party': 'Name of the Political Party'},
                  category_orders={'Name of the Political Party': sorted_purchasers})
    fig2.show()
def plot_yearly_data(df, year, data_column, title_prefix):
    df_year = df[df['Year'] == year].copy()
    sorted_purchasers = df_year.groupby('Name of the Political Party')[data_column].sum().sort_values(ascending=False).index
    fig = px.bar(df_year, x='Date of Encashment', y=data_column, color='Name of the Political Party',
                 title=f'{title_prefix} - {year}',
                 labels={'Date of Encashment': 'Date', data_column: title_prefix,
                         'Name of the Political Party': 'Name of the Political Party'},
                 category_orders={'Name of the Political Party': sorted_purchasers})
    fig.update_layout(height=800, width=1000)
    fig.update_xaxes(type='category')
    fig.show()
    
def plot_yearly_data_combined(df_daywiseTransactions_party):
    unique_years = sorted(df_daywiseTransactions_party['Year'].unique())
    for year in unique_years:
        plot_yearly_data(df_daywiseTransactions_party, year, 'TotalDenomination', 'Yearly Transaction Value by Name of the Political Party')
        plot_yearly_data(df_daywiseTransactions_party, year, 'TotalTransactions', 'Yearly Purchase Count by Name of the Political Party')
        print("============================================================ End of Year ", year, "============================================================")

def create_bar_chart(df_combinedDenomination_party):
    df_sorted = df_combinedDenomination_party.sort_values(by='CombinedDenomination', ascending=False)
    fig = px.bar(df_sorted, x='Name of the Political Party', y='CombinedDenomination', 
                 title='Total Transaction Value by Political Parties',
                 labels={'CombinedDenomination': 'Total Transaction Value', 'Name of the Political Party': 'Political Party'},
                 color='Name of the Political Party',
                 color_discrete_sequence=px.colors.qualitative.Plotly)
    fig.update_layout(xaxis_title=None, yaxis_title=None, showlegend=False)
    return fig

def create_scatter_plot(df_combinedDenomination_party):
    # Sort data by CombinedDenomination in descending order
    df_sorted = df_combinedDenomination_party.sort_values(by='CombinedDenomination', ascending=False)
    fig = px.scatter(df_sorted, x='Name of the Political Party', y='CombinedDenomination', 
                     title='Total Transaction Value by Political Parties',
                     labels={'CombinedDenomination': 'Total Transaction Value', 'Name of the Political Party': 'Political Party'},
                     color='Name of the Political Party',
                     color_discrete_sequence=px.colors.qualitative.Plotly,
                     hover_name='Name of the Political Party',
                     size='CombinedDenomination',
                     size_max=50)
    fig.update_layout(xaxis_title=None, yaxis_title=None, showlegend=False)
    return fig

def create_pie_chart(df_combinedDenomination_party):
    df_sorted = df_combinedDenomination_party.sort_values(by='CombinedDenomination', ascending=False)
    # Create a pie chart
    fig = px.pie(df_sorted, values='CombinedDenomination', names='Name of the Political Party', 
                 title='Total Transaction Value Distribution Among Political Parties',
                 color_discrete_sequence=px.colors.qualitative.Plotly)
    fig.update_traces(textposition='inside', textinfo='percent+label', pull=[0.05] * len(df_sorted))
    fig.update_layout(showlegend=False)
    return fig

def create_cumulative_purchase_treemap(df_combinedDenomination_party, df_daywiseTransactions_party):
    top_purchasers = df_daywiseTransactions_party.groupby('Name of the Political Party')['TotalTransactions'].max().index
    df_top = df_daywiseTransactions_party[df_daywiseTransactions_party['Name of the Political Party'].isin(top_purchasers)]
    df_merged = pd.merge(df_top, df_combinedDenomination_party, on='Name of the Political Party', how='left')
    fig = px.treemap(df_merged, path=['Name of the Political Party', 'Date of Encashment'], values='TotalDenomination', color='TotalDenomination',
                     title='Total Transaction Value Over Time for Political Parties',
                     labels={'TotalDenomination': 'Total Transaction Value', 'TotalTransactions': 'Cumulative Purchase Count'},
                     hover_data={'TotalDenomination': True, 'TotalTransactions': True},
                     width=1200, height=1200)
    return fig


## 3.2 Party Data Visualization

### Plot 3.2.a: Quarterly Transaction Value and Quarterly Transaction Frequency by the companies

In [ ]:
unique_years = df_daywiseTransactions_party['Year'].unique()
for year in unique_years:
    plot_quarterly_data(df_daywiseTransactions_party, year)

### Plot3.2.b: Yearly Transaction Value and Yearly Transaction Frequency by the companies

In [ ]:
# plotting yearly transaction value and yearly transaction frequency by the companies
plot_yearly_data_combined(df_daywiseTransactions_party)

============================================================ End of Year  2019 ============================================================


============================================================ End of Year  2020 ============================================================


============================================================ End of Year  2021 ============================================================


============================================================ End of Year  2022 ============================================================


============================================================ End of Year  2023 ============================================================


============================================================ End of Year  2024 ============================================================


### Plot 3.2.c: Total Transaction Value Over Time for Parties

In [ ]:
fig = create_cumulative_purchase_treemap(df_combinedDenomination_party, df_daywiseTransactions_party)
fig.show()


### Plot 3.2.d: Other Data Visualization for Political Parties

In [ ]:
fig_bar = create_bar_chart(df_combinedDenomination_party)
fig_pie = create_pie_chart(df_combinedDenomination_party)

fig_bar.show()
fig_pie.show()


In [ ]:
fig_scatter = create_scatter_plot(df_combinedDenomination_party)
fig_scatter.show()
